<a href="https://colab.research.google.com/github/iject/SB3/blob/main/diploma/diploma.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Скачивание библиотек

In [5]:
!pip install stable-baselines3[extra];
!pip install gymnasium;
!pip install gymnasium[mujoco];
# !pip install ipywidgets
# !pip install optuna

In [6]:
!pip list

Package                               Version
------------------------------------- ------------------
absl-py                               1.4.0
accelerate                            1.6.0
aiohappyeyeballs                      2.6.1
aiohttp                               3.11.15
aiosignal                             1.3.2
alabaster                             1.0.0
albucore                              0.0.24
albumentations                        2.0.6
ale-py                                0.11.0
altair                                5.5.0
annotated-types                       0.7.0
antlr4-python3-runtime                4.9.3
anyio                                 4.9.0
argon2-cffi                           23.1.0
argon2-cffi-bindings                  21.2.0
array_record                          0.7.2
arviz                                 0.21.0
astropy                               7.0.1
astropy-iers-data                     0.2025.5.5.0.38.14
astunparse                            1.6

# Импорт библиотек

In [7]:
%load_ext tensorboard
import gymnasium as gym
import sys, os

# from stable_baselines3 import A2C, TD3, PPO, SAC
from stable_baselines3 import SAC
from stable_baselines3.common.evaluation import evaluate_policy
from stable_baselines3.common.vec_env import DummyVecEnv, SubprocVecEnv, VecMonitor
from stable_baselines3.common.monitor import Monitor
from stable_baselines3.common.env_util import make_vec_env
from stable_baselines3.common.callbacks import CheckpointCallback, EvalCallback

# import matplotlib.pyplot as plt
import numpy as np
# import pandas as pd

# from IPython.display import clear_output

# import time

In [ ]:
log_dir = "/tmp/gym/"
os.makedirs(log_dir, exist_ok=True)

In [ ]:
path_to_xml_file = os.path.join(log_dir, "ant_my_v1.xml")
custom_env_kwargs = {"xml_file": path_to_xml_file, "ctrl_cost_weight": 0.5,
                      "healthy_reward": 0} # для передачи в make_vec_env
render_env_kwargs = {"render_mode": "rgb_array", "width": 1280, "height": 720}
seed = 0

env = gym.make('Ant-v5', **render_env_kwargs, **custom_env_kwargs)

observation, info = env.reset(seed=seed)

env.action_space.seed(seed) # set action space seed

episode_over = False
while not episode_over:
    action = env.action_space.sample()  # agent policy that uses the observation and info
    observation, reward, terminated, truncated, info = env.step(action)
    # clear_output(True)
    # plt.imshow(env.render())
    # plt.show()

    episode_over = terminated or truncated

print(env.action_space)
print(env.observation_space)

env.close()

Box([-0.524  0.524 -0.524  0.524 -0.524 -1.22  -0.524 -1.22 ], [ 0.524  1.22   0.524  1.22   0.524 -0.524  0.524 -0.524], (8,), float32)
Box(-inf, inf, (105,), float64)


In [ ]:
# для быстрой проверки использую класс DummyVecEnv (потом SubprocVecEnv)
vec_env = make_vec_env('Ant-v5', env_kwargs=custom_env_kwargs, seed=seed, n_envs=4, vec_env_cls=SubprocVecEnv)

In [ ]:
print(vec_env.get_attr('env'))
print(vec_env.get_attr('action_space'))
print(vec_env.get_attr('np_random_seed'))

[<TimeLimit<OrderEnforcing<PassiveEnvChecker<AntEnv instance>>>>, <TimeLimit<OrderEnforcing<PassiveEnvChecker<AntEnv instance>>>>, <TimeLimit<OrderEnforcing<PassiveEnvChecker<AntEnv instance>>>>, <TimeLimit<OrderEnforcing<PassiveEnvChecker<AntEnv instance>>>>]
[Box([-0.524  0.524 -0.524  0.524 -0.524 -1.22  -0.524 -1.22 ], [ 0.524  1.22   0.524  1.22   0.524 -0.524  0.524 -0.524], (8,), float32), Box([-0.524  0.524 -0.524  0.524 -0.524 -1.22  -0.524 -1.22 ], [ 0.524  1.22   0.524  1.22   0.524 -0.524  0.524 -0.524], (8,), float32), Box([-0.524  0.524 -0.524  0.524 -0.524 -1.22  -0.524 -1.22 ], [ 0.524  1.22   0.524  1.22   0.524 -0.524  0.524 -0.524], (8,), float32), Box([-0.524  0.524 -0.524  0.524 -0.524 -1.22  -0.524 -1.22 ], [ 0.524  1.22   0.524  1.22   0.524 -0.524  0.524 -0.524], (8,), float32)]
[318075917486807154733397746473158945427, 76848677455367256094175303224587581619, 94277393536856918306222469569272911688, 262329583993313277724160917684311102316]


In [ ]:
%%time
model = A2C("MlpPolicy", vec_env, verbose=0, seed=seed)
model.learn(total_timesteps=50_000, progress_bar=True);

Output()

/usr/local/lib/python3.11/dist-packages/ipywidgets/widgets/widget_output.py:111: DeprecationWarning: 
Kernel._parent_header is deprecated in ipykernel 6. Use .get_parent()
  if ip and hasattr(ip, 'kernel') and hasattr(ip.kernel, '_parent_header'):

CPU times: user 50.3 s, sys: 2.39 s, total: 52.7 s
Wall time: 1min 36s


In [ ]:
%%time
env = gym.make('Ant-v5', **custom_env_kwargs)
observation, info = env.reset(seed=seed)
env.action_space.seed(seed) # set action space seed

# eval_env = Monitor(gym.make("Ant-v5", **custom_env_kwargs))
eval_env = Monitor(env)
print(eval_env.env.action_space)

mean_reward, std_reward = evaluate_policy(model, eval_env, n_eval_episodes=10)
print(f"{mean_reward = }, {std_reward = }")

mean_reward, std_reward = evaluate_policy(model, vec_env, n_eval_episodes=10)
print(f"{mean_reward = }, {std_reward = }")

env.close()
eval_env.close()
# vec_env.close()

Box([-0.524  0.524 -0.524  0.524 -0.524 -1.22  -0.524 -1.22 ], [ 0.524  1.22   0.524  1.22   0.524 -0.524  0.524 -0.524], (8,), float32)
mean_reward = np.float64(4.2307243), std_reward = np.float64(5.764570964688821)
mean_reward = np.float64(8.454294400000002), std_reward = np.float64(8.525102646037304)
CPU times: user 207 ms, sys: 7.78 ms, total: 215 ms
Wall time: 299 ms


# Пробую SAC
## Узнаю, что быстрее работает

In [ ]:
env_id = "Ant-v5"

env_types = ["mono", "dummy", "subproc"]
timing_dict = {i: [] for i in env_types}
timing_dict['cell_name'] = []
print(timing_dict)

{'mono': [], 'dummy': [], 'subproc': [], 'cell_name': []}


In [ ]:
timing_dict['cell_name'].append("create env")

In [ ]:
%%time
start_time = time.time()
learning_env_mono = gym.make(env_id)
end_time = time.time()

execution_time = end_time - start_time
timing_dict["mono"].append(execution_time)

CPU times: user 217 ms, sys: 33.8 ms, total: 251 ms
Wall time: 362 ms


In [ ]:
%%time
start_time = time.time()
learning_env_dummy = make_vec_env(env_id, n_envs=4, vec_env_cls=DummyVecEnv)
end_time = time.time()

execution_time = end_time - start_time
timing_dict["dummy"].append(execution_time)

CPU times: user 17.7 ms, sys: 2.98 ms, total: 20.7 ms
Wall time: 20.8 ms


In [ ]:
%%time
start_time = time.time()
learning_env_subproc = make_vec_env(env_id, n_envs=4, vec_env_cls=SubprocVecEnv)
end_time = time.time()

execution_time = end_time - start_time
timing_dict["subproc"].append(execution_time)

CPU times: user 160 ms, sys: 27.3 ms, total: 187 ms
Wall time: 38.4 s


In [ ]:
timing_dict

{'mono': [0.3621094226837158],
 'dummy': [0.020691871643066406],
 'subproc': [38.430933713912964],
 'cell_name': ['create env']}

In [ ]:
timing_dict['cell_name'].append("create and learn model")
timing_dict['cell_name'].append("check result")

timing_dict["mean_reward"] = []
timing_dict["std_reward"] = []
timing_dict["total_timesteps"] = []

In [ ]:
eval_env = Monitor(gym.make(env_id))
n_timesteps = 1000

for l_env, name in zip([learning_env_mono, learning_env_dummy, learning_env_subproc],
                                    env_types):
  # create and learn model
  start_time = time.time()
  model = SAC("MlpPolicy", env=l_env, verbose=0)
  model.learn(total_timesteps=n_timesteps)
  end_time = time.time()

  execution_time = end_time - start_time
  timing_dict[name].append(execution_time)

  # check result
  start_time = time.time()
  mean_reward, std_reward = evaluate_policy(model, eval_env, n_eval_episodes=10)
  end_time = time.time()

  execution_time = end_time - start_time
  timing_dict[name].append(execution_time)
  timing_dict["mean_reward"].append(mean_reward)
  timing_dict["std_reward"].append(std_reward)
  timing_dict["total_timesteps"].append(n_timesteps)

  print(f"{mean_reward = }, {std_reward = }")

  del model

mean_reward = np.float64(960.9022848000001), std_reward = np.float64(1.1576846971743928)
mean_reward = np.float64(991.8032104), std_reward = np.float64(3.411878978957601)
mean_reward = np.float64(992.365478), std_reward = np.float64(1.605938761179)


In [ ]:
%pwd

'/content'

In [ ]:
display(timing_dict)
df = pd.DataFrame(timing_dict, columns=env_types, index=timing_dict["cell_name"])
df.loc["total_timesteps"] = timing_dict["total_timesteps"]
df.loc["mean_reward"] = timing_dict["mean_reward"]
df.loc["std_reward"] = timing_dict["std_reward"]
df.to_csv("CPU.csv")
df

{'mono': [0.3621094226837158, 36.91819524765015, 13.848880290985107],
 'dummy': [0.020691871643066406, 8.224994897842407, 13.910984992980957],
 'subproc': [38.430933713912964, 8.040517568588257, 13.345988035202026],
 'cell_name': ['create env', 'create and learn model', 'check result'],
 'mean_reward': [np.float64(960.9022848000001),
  np.float64(991.8032104),
  np.float64(992.365478)],
 'std_reward': [np.float64(1.1576846971743928),
  np.float64(3.411878978957601),
  np.float64(1.605938761179)],
 'total_timesteps': [1000, 1000, 1000]}

mono        dummy      subproc
create env                 0.362109     0.020692    38.430934
create and learn model    36.918195     8.224995     8.040518
check result              13.848880    13.910985    13.345988
total_timesteps         1000.000000  1000.000000  1000.000000
mean_reward              960.902285   991.803210   992.365478
std_reward                 1.157685     3.411879     1.605939

In [ ]:
pd.read_csv("T4 GPU.csv")

Unnamed: 0         mono        dummy      subproc
0       create env     0.474318     0.024088    35.636837
1     create model    21.244399     3.304012     3.203128
2     check result    15.676393    14.838188    14.410740
3  total_timesteps  1000.000000  1000.000000  1000.000000
4      mean_reward   902.738335   984.487125   987.341328
5       std_reward    39.861654     2.508520     2.391376

In [ ]:
display(timing_dict)
df = pd.DataFrame(timing_dict, columns=env_types, index=timing_dict["cell_name"])
df.loc["total_timesteps"] = timing_dict["total_timesteps"]
df.loc["mean_reward"] = timing_dict["mean_reward"]
df.loc["std_reward"] = timing_dict["std_reward"]
df.to_csv("CPU.csv")
df

{'mono': [0.010192155838012695, 40.50720143318176, 15.51898193359375],
 'dummy': [0.019891738891601562, 9.603487014770508, 15.254503011703491],
 'subproc': [28.817936420440674, 9.874634027481079, 14.902720928192139],
 'cell_name': ['create env', 'create model', 'check result'],
 'mean_reward': [np.float64(963.8743709),
  np.float64(995.2997011),
  np.float64(990.0333390000002)],
 'std_reward': [np.float64(7.855395704675203),
  np.float64(2.954399461891997),
  np.float64(4.280491535890196)],
 'total_timesteps': [1000, 1000, 1000]}

mono        dummy      subproc
create env          0.010192     0.019892    28.817936
create model       40.507201     9.603487     9.874634
check result       15.518982    15.254503    14.902721
total_timesteps  1000.000000  1000.000000  1000.000000
mean_reward       963.874371   995.299701   990.033339
std_reward          7.855396     2.954399     4.280492

## Обучаю SAC


### Смотрю, какой VecEnv быстрее

In [ ]:
env_id = "Ant-v5"
n_timesteps = 1000
n_envs = 4

In [ ]:
%%time
train_env_subproc = make_vec_env(env_id, n_envs=n_envs, vec_env_cls=SubprocVecEnv)


CPU times: user 384 ms, sys: 70.1 ms, total: 454 ms
Wall time: 1min 30s


In [ ]:
%%time
train_env_dummy = make_vec_env(env_id, n_envs=n_envs, vec_env_cls=DummyVecEnv)

CPU times: user 36.4 ms, sys: 32 µs, total: 36.4 ms
Wall time: 41.2 ms


In [ ]:
%time model = SAC("MlpPolicy", env=train_env_subproc, verbose=0)
%timeit model.learn(total_timesteps=n_timesteps)

CPU times: user 12 ms, sys: 7.02 ms, total: 19 ms
Wall time: 23.8 ms
4.8 s ± 444 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [ ]:
%time model = SAC("MlpPolicy", env=train_env_dummy, verbose=0)
%timeit model.learn(total_timesteps=n_timesteps)

CPU times: user 17.7 ms, sys: 20 ms, total: 37.7 ms
Wall time: 37.5 ms
6.56 s ± 257 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [ ]:
train_env_subproc.close()
train_env_dummy.close()

In [ ]:
for n_envs in [4, 8, 16, 32, 64]:
  print(f"{n_envs = }")
  %time train_env_dummy = make_vec_env(env_id, n_envs=n_envs, vec_env_cls=DummyVecEnv)
  %time model = SAC("MlpPolicy", env=train_env_dummy, verbose=0)
  %timeit model.learn(total_timesteps=n_timesteps)

  train_env_dummy.close()


n_envs = 4
CPU times: user 18.7 ms, sys: 0 ns, total: 18.7 ms
Wall time: 18 ms
CPU times: user 19.5 ms, sys: 3.97 ms, total: 23.4 ms
Wall time: 23.4 ms
3.69 s ± 262 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
n_envs = 8
CPU times: user 26.4 ms, sys: 7 µs, total: 26.4 ms
Wall time: 26.2 ms
CPU times: user 12.5 ms, sys: 991 µs, total: 13.5 ms
Wall time: 13.5 ms
2.14 s ± 273 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
n_envs = 16
CPU times: user 51.4 ms, sys: 987 µs, total: 52.4 ms
Wall time: 52 ms
CPU times: user 11.3 ms, sys: 0 ns, total: 11.3 ms
Wall time: 11.3 ms
1.24 s ± 50.4 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
n_envs = 32
CPU times: user 132 ms, sys: 15 ms, total: 147 ms
Wall time: 167 ms
CPU times: user 13.7 ms, sys: 9.02 ms, total: 22.8 ms
Wall time: 22.8 ms
895 ms ± 71.5 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
n_envs = 64
CPU times: user 204 ms, sys: 24.1 ms, total: 228 ms
Wall time: 227 ms
CPU times: user 12.7 ms, sys: 4.01 ms,

### Обучаю SAC

In [ ]:
%%timeit
train_env_dummy = make_vec_env(env_id, n_envs=n_envs*2, vec_env_cls=DummyVecEnv)

model = SAC("MlpPolicy", env=train_env_dummy, verbose=0)
model.learn(total_timesteps=n_timesteps)

1.93 s ± 145 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [ ]:
%%time
# model = SAC("MlpPolicy", env=train_env_dummy, verbose=0, batch_size=10_000)
train_env_dummy = make_vec_env(env_id, n_envs=n_envs*2, vec_env_cls=DummyVecEnv)
model = SAC("MlpPolicy", env=train_env_dummy, verbose=0)

model.learn(total_timesteps=500_000, progress_bar=True)

 100% ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╸ 499,928/500,000  [ 0:18:11 < 0:00:01 , 459 it/s ]

CPU times: user 17min 34s, sys: 12.7 s, total: 17min 47s
Wall time: 18min 11s


In [ ]:
model.save(r"SAC_500_000_timesteps")

In [ ]:
%time
env = gym.make(env_id)
eval_env = Monitor(env)

mean_reward, std_reward = evaluate_policy(model, eval_env)
print(f"mean_reward: {mean_reward:.2f} +/- {std_reward:.2f}")

env.close()
eval_env.close()

CPU times: user 2 µs, sys: 0 ns, total: 2 µs
Wall time: 5.72 µs
mean_reward: 1598.01 +/- 378.16


### Prepare video recording

In [ ]:
# Set up fake display; otherwise rendering will fail
import os
os.system("Xvfb :1 -screen 0 1024x768x24 &")
os.environ['DISPLAY'] = ':1'

In [ ]:
import base64
from pathlib import Path

from IPython import display as ipythondisplay


def show_videos(video_path="", prefix=""):
    """
    Taken from https://github.com/eleurent/highway-env

    :param video_path: (str) Path to the folder containing videos
    :param prefix: (str) Filter the video, showing only the only starting with this prefix
    """
    html = []
    for mp4 in Path(video_path).glob("{}*.mp4".format(prefix)):
        video_b64 = base64.b64encode(mp4.read_bytes())
        html.append(
            """<video alt="{}" autoplay
                    loop controls style="height: 400px;">
                    <source src="data:video/mp4;base64,{}" type="video/mp4" />
                </video>""".format(
                mp4, video_b64.decode("ascii")
            )
        )
    ipythondisplay.display(ipythondisplay.HTML(data="<br>".join(html)))

We will record a video using the [VecVideoRecorder](https://stable-baselines3.readthedocs.io/en/master/guide/vec_envs.html#vecvideorecorder) wrapper, you will learn about those wrapper in the next notebook.

In [ ]:
from stable_baselines3.common.vec_env import VecVideoRecorder, DummyVecEnv


def record_video(env_id, model, video_length=500, prefix="", video_folder="videos/"):
    """
    :param env_id: (str)
    :param model: (RL model)
    :param video_length: (int)
    :param prefix: (str)
    :param video_folder: (str)
    """
    eval_env = DummyVecEnv([lambda: gym.make(env_id, render_mode="rgb_array")])
    # Start the video at step=0 and record 500 steps
    eval_env = VecVideoRecorder(
        eval_env,
        video_folder=video_folder,
        record_video_trigger=lambda step: step == 0,
        video_length=video_length,
        name_prefix=prefix,
    )

    obs = eval_env.reset()
    for _ in range(video_length):
        action, _ = model.predict(obs)
        obs, _, _, _ = eval_env.step(action)

    # Close the video recorder
    eval_env.close()

### Visualize trained agent



In [ ]:
record_video(ENV_ID, model, video_length=500, prefix=f"SAC-{ENV_ID}")

NameError: name 'record_video' is not defined

In [ ]:
show_videos("videos", prefix="SAC")

## Навороченное обучение SAC

**TODO:**
+ Увеличить n_procs(n_envs) до 24

### Удаление файлов из своих папок-storage

In [ ]:
all_dirs = os.listdir()
all_dirs

['.config', 'callback_storage', 'tb_storage', 'monitor_storage', 'sample_data']

In [ ]:
all_dirs.remove('.config')
all_dirs.remove('sample_data')
all_dirs

['callback_storage', 'tb_storage', 'monitor_storage']

In [ ]:
import glob
import shutil


# for dir in all_dirs:
#   for i in os.listdir(dir):
#     i = os.path.join(dir, i)
#     for j in os.listdir(i):
#       j = os.path.join(i, j)
      # os.remove(j)

if input("Введи del для удаления папок: ") != 'del': raise Exception

for dir in all_dirs:
  shutil.rmtree(dir)

### Обучение

In [ ]:
ENV_ID = "Ant-v5"
N_TIMESTEPS = 1e6
ALGO = SAC
n_procs = 4 # попробовать 4 * 6 процессов
N_EVALUATIONS = 10 # каждый 100_00 шаг
N_CHECKPOINTS = 10 # каждый 100_00 шаг
eval_freq = int(N_TIMESTEPS / N_EVALUATIONS)
save_freq = int(N_TIMESTEPS / N_CHECKPOINTS)
n_envs = n_procs

# default values:
#  learning_starts=100
hyperparams_zoo = dict(learning_starts = 10_000) # взято из репозитория sb_zoo

In [ ]:
monitors_storage_path = "monitor_storage"
tb_storage_path = "tb_storage"
callback_storage_path = "callback_storage"

os.makedirs(monitors_storage_path, exist_ok=True)
os.makedirs(tb_storage_path, exist_ok=True)
os.makedirs(callback_storage_path, exist_ok=True)

train_monitor_path = os.path.join(monitors_storage_path, "train_monitor")
eval_monitor_path = os.path.join(monitors_storage_path, "eval_monitor")

eval_callback_path = os.path.join(callback_storage_path, "eval_callback")
checkpoint_callback_path = os.path.join(callback_storage_path, "checkpoint_callback")

In [ ]:
train_env = make_vec_env(ENV_ID, n_procs, monitor_dir=train_monitor_path)
# train_env = VecMonitor(train_env, train_monitor_path)
eval_env = make_vec_env(ENV_ID, n_procs, monitor_dir=eval_monitor_path)
# eval_env = VecMonitor(eval_env, train_monitor_path)

eval_callback = EvalCallback(eval_env,
                             best_model_save_path=eval_callback_path,
                             log_path=eval_callback_path,
                             eval_freq=max(eval_freq // n_envs, 1))


checkpoint_callback = CheckpointCallback(
  save_freq=max(save_freq // n_envs, 1),
  save_path=checkpoint_callback_path,
  name_prefix="SAC_test",
  save_replay_buffer=True,
  save_vecnormalize=True,
)

In [ ]:
%%time
model = ALGO("MlpPolicy", train_env, **hyperparams_zoo,
            tensorboard_log=tb_storage_path)

model.learn(N_TIMESTEPS, tb_log_name=f"{ALGO.__name__}_{N_TIMESTEPS}_timesteps",
            callback=[eval_callback, checkpoint_callback],
            progress_bar=True)

 100% ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1,000,000/1,000,000  [ 3:00:48 < 0:00:00 , 48 it/s ]

CPU times: user 2h 52min 36s, sys: 1min 33s, total: 2h 54min 10s
Wall time: 3h 48s


In [ ]:
display(eval_callback.n_calls, checkpoint_callback.n_calls)
display(eval_callback.num_timesteps, checkpoint_callback.num_timesteps)

250000

250000

1000000

1000000

In [ ]:
!zip -r /content/all_content.zip /content

from google.colab import files
files.download("/content/all_content.zip");

  adding: content/ (stored 0%)
  adding: content/.config/ (stored 0%)
  adding: content/.config/.last_update_check.json (deflated 22%)
  adding: content/.config/active_config (stored 0%)
  adding: content/.config/logs/ (stored 0%)
  adding: content/.config/logs/2025.05.12/ (stored 0%)
  adding: content/.config/logs/2025.05.12/13.37.07.817575.log (deflated 86%)
  adding: content/.config/logs/2025.05.12/13.36.34.925125.log (deflated 93%)
  adding: content/.config/logs/2025.05.12/13.37.18.051962.log (deflated 57%)
  adding: content/.config/logs/2025.05.12/13.37.09.418759.log (deflated 58%)
  adding: content/.config/logs/2025.05.12/13.37.18.758811.log (deflated 56%)
  adding: content/.config/logs/2025.05.12/13.36.58.869156.log (deflated 58%)
  adding: content/.config/.last_opt_in_prompt.yaml (stored 0%)
  adding: content/.config/hidden_gcloud_config_universe_descriptor_data_cache_configs.db (deflated 97%)
  adding: content/.config/config_sentinel (stored 0%)
  adding: content/.config/confi

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
from google.colab import drive
drive.mount('/content/drive/MyDrive/Colab_Notebooks')

ValueError: Mountpoint must be in a directory that exists

In [ ]:

drive.flush_and_unmount()


In [ ]:
train_env.close()
eval_env.close()

In [ ]:
# %tensorboard --logdir tb_storage
!kill 3978

In [ ]:
from tensorboard import notebook
notebook.list()
notebook.display(port=6006, height=1000)

In [ ]:
# !zip -r tb_storage.zip tb_storage

from google.colab import files
files.download("/content/tb_storage.zip")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
# from stable_baselines3.common.results_plotter import
from stable_baselines3.common.monitor import load_results, get_monitor_files

get_monitor_files(os.path.join(monitors_storage_path, "eval_monitor"))
load_results(os.path.join(monitors_storage_path, "eval_monitor"))

### Результат

In [ ]:
mean_reward, std_reward = evaluate_policy(model, model.get_env(), n_eval_episodes=10)
print(f"{mean_reward = }, {std_reward = }")

mean_reward = np.float64(1237.6630582), std_reward = np.float64(879.7674676146113)


In [ ]:
record_video(ENV_ID, model, video_length=500, prefix=f"SAC-{ENV_ID}")

Saving video to /content/videos/SAC-Ant-v5-step-0-to-step-500.mp4


/usr/local/lib/python3.11/dist-packages/moviepy/config_defaults.py:1: DeprecationWarning: invalid escape sequence '\P'
  """


Moviepy - Building video /content/videos/SAC-Ant-v5-step-0-to-step-500.mp4.
Moviepy - Writing video /content/videos/SAC-Ant-v5-step-0-to-step-500.mp4



Moviepy - Done !
Moviepy - video ready /content/videos/SAC-Ant-v5-step-0-to-step-500.mp4


In [ ]:
show_videos("videos", prefix="SAC")

## Автоматизированное обучение SAC

**TODO:**
+ Увеличить n_procs(n_envs) до 24

In [ ]:
# может пригодится

# storage_list = [x for x in globals().keys() if "storage" in x]

### Функции

In [47]:
import glob
import shutil


def create_storage_folders(create=True):
  """
  Функция для создания папок-хранилищ и возвращения списка всех папок

  :return: Словарь с папками в иерархическом порядке
  """

  # Главные папки-хранилища
  storages_dict = {"monitor_dir": "monitor_storage",
                  "callback_dir": "callback_storage",
                  "tb_dir": "tb_storage",
                   }
  if create:
    os.makedirs(storages_dict["monitor_dir"], exist_ok=True)
    os.makedirs(storages_dict["callback_dir"], exist_ok=True)
    os.makedirs(storages_dict["tb_dir"], exist_ok=True)

  # Папки для train монитора и eval монитора
  monitors_dict = {"train": os.path.join(storages_dict["monitor_dir"], "train_monitor"),
                   "eval": os.path.join(storages_dict["monitor_dir"], "eval_monitor")}

  # Папки для train монитора и eval монитора
  callbacks_dict = {"eval": os.path.join(storages_dict["callback_dir"], "eval_callback"),
                    "checkpont": os.path.join(storages_dict["callback_dir"], "checkpoint_callback")}

  # Папка для tensorboard
  tb_dict = {"experiment": os.path.join(storages_dict["tb_dir"], "experiment_folder")}

  return storages_dict, monitors_dict, callbacks_dict, tb_dict


def delete_storage_folders(storage_folders, verbose = 0):
  """Функция для удаления папок-хранилищ"""

  if verbose == 1: print(storage_folders)

  if input("Введи 'del' для удаления папок: ") != 'del': raise Exception

  for folder in storage_folders:
    shutil.rmtree(folder)

### Обучение

In [48]:
ENV_ID = "Ant-v5"
ALGO = SAC

N_TIMESTEPS = 1e3
N_ENVS = 4 * 6 # попробовать 4 * 6 процессов
N_EVALUATIONS = 2 # каждый 100_00 шаг
N_CHECKPOINTS = 2 # каждый 100_00 шаг
EVAL_FREQ = max(int(N_TIMESTEPS / N_EVALUATIONS) // N_ENVS, 1)
SAVE_FREQ = max(int(N_TIMESTEPS / N_CHECKPOINTS) // N_ENVS, 1)

checkpoint_callback_name_prefix = "SAC_test"

# default values:
#  learning_starts=100
hyperparams_zoo = dict(learning_starts = 10_000) # взято из репозитория sb_zoo

In [49]:
delete_storage_folders(create_storage_folders(False)[0].values())

Введи 'del' для удаления папок: del


In [50]:
storages_dict, monitors_dict, callbacks_dict, tb_dict = create_storage_folders()

In [51]:
train_env = make_vec_env(ENV_ID, N_ENVS, monitor_dir=monitors_dict["train"])
eval_env = make_vec_env(ENV_ID, N_ENVS, monitor_dir=monitors_dict["eval"])

eval_callback = EvalCallback(eval_env,
                             best_model_save_path=callbacks_dict["eval"],
                             log_path=eval_callback_path,
                             eval_freq=EVAL_FREQ)


checkpoint_callback = CheckpointCallback(save_freq=SAVE_FREQ,
                                         save_path=callbacks_dict["checkpont"],
                                         name_prefix=checkpoint_callback_name_prefix,
                                         save_replay_buffer=True,
                                         save_vecnormalize=True,)

In [52]:
%%time
model = ALGO("MlpPolicy", train_env, **hyperparams_zoo,
            tensorboard_log=tb_dict["experiment"])

model.learn(N_TIMESTEPS, tb_log_name=f"{ALGO.__name__}_{int(N_TIMESTEPS)}_timesteps",
            callback=[eval_callback, checkpoint_callback],
            progress_bar=True)

Output()

/usr/local/lib/python3.11/dist-packages/ipywidgets/widgets/widget_output.py:111: DeprecationWarning: 
Kernel._parent_header is deprecated in ipykernel 6. Use .get_parent()
  if ip and hasattr(ip, 'kernel') and hasattr(ip.kernel, '_parent_header'):

Eval num_timesteps=480, episode_reward=985.90 +/- 3.72

Episode length: 1000.00 +/- 0.00

New best mean reward!

Eval num_timesteps=960, episode_reward=984.72 +/- 2.74

Episode length: 1000.00 +/- 0.00

CPU times: user 40.4 s, sys: 10.3 s, total: 50.7 s
Wall time: 1min 12s


In [ ]:
!zip -r /content/all_content.zip /content

from google.colab import files
files.download("/content/all_content.zip");

In [56]:
from google.colab import drive
# drive.mount('/content/drive/MyDrive/Colab_Notebooks')
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:

drive.flush_and_unmount()


In [ ]:
train_env.close()
eval_env.close()

In [ ]:
# %tensorboard --logdir tb_storage
!kill 3978

In [ ]:
from tensorboard import notebook
notebook.list()
notebook.display(port=6006, height=1000)

In [ ]:
# !zip -r tb_storage.zip tb_storage

from google.colab import files
files.download("/content/tb_storage.zip")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
# from stable_baselines3.common.results_plotter import
from stable_baselines3.common.monitor import load_results, get_monitor_files

get_monitor_files(os.path.join(monitors_storage_path, "eval_monitor"))
load_results(os.path.join(monitors_storage_path, "eval_monitor"))

## Результат

In [ ]:
mean_reward, std_reward = evaluate_policy(model, model.get_env(), n_eval_episodes=10)
print(f"{mean_reward = }, {std_reward = }")

mean_reward = np.float64(1237.6630582), std_reward = np.float64(879.7674676146113)


In [ ]:
record_video(ENV_ID, model, video_length=500, prefix=f"SAC-{ENV_ID}")

Saving video to /content/videos/SAC-Ant-v5-step-0-to-step-500.mp4


/usr/local/lib/python3.11/dist-packages/moviepy/config_defaults.py:1: DeprecationWarning: invalid escape sequence '\P'
  """


Moviepy - Building video /content/videos/SAC-Ant-v5-step-0-to-step-500.mp4.
Moviepy - Writing video /content/videos/SAC-Ant-v5-step-0-to-step-500.mp4



Moviepy - Done !
Moviepy - video ready /content/videos/SAC-Ant-v5-step-0-to-step-500.mp4


In [ ]:
show_videos("videos", prefix="SAC")

# Пробую TD3

In [ ]:
%%time
vec_env = make_vec_env('Ant-v5', env_kwargs=None, seed=None, n_envs=4, vec_env_cls=SubprocVecEnv)

In [ ]:
print(vec_env.get_attr('env'))
print(vec_env.get_attr('action_space'))
print(vec_env.get_attr('np_random_seed'))

[<TimeLimit<OrderEnforcing<PassiveEnvChecker<AntEnv instance>>>>, <TimeLimit<OrderEnforcing<PassiveEnvChecker<AntEnv instance>>>>, <TimeLimit<OrderEnforcing<PassiveEnvChecker<AntEnv instance>>>>, <TimeLimit<OrderEnforcing<PassiveEnvChecker<AntEnv instance>>>>]
[Box(-1.0, 1.0, (8,), float32), Box(-1.0, 1.0, (8,), float32), Box(-1.0, 1.0, (8,), float32), Box(-1.0, 1.0, (8,), float32)]
[48974919311829556210278245614870816953, 310378350735749337282864663740274950296, 29316829094447057129193289095539400376, 220056835590822699796813948177469902549]


In [ ]:
%%time
model = TD3("MlpPolicy", vec_env, verbose=0, seed=seed)
model.learn(total_timesteps=50_000, progress_bar=True);

Output()

/usr/local/lib/python3.11/dist-packages/ipywidgets/widgets/widget_output.py:111: DeprecationWarning: 
Kernel._parent_header is deprecated in ipykernel 6. Use .get_parent()
  if ip and hasattr(ip, 'kernel') and hasattr(ip.kernel, '_parent_header'):

CPU times: user 8min 23s, sys: 5.79 s, total: 8min 29s
Wall time: 9min 40s


In [ ]:
%%time
# env = gym.make('Ant-v5', **custom_env_kwargs)
env = gym.make('Ant-v5')
observation, info = env.reset(seed=None)
env.action_space.seed(seed=None) # set action space seed

# eval_env = Monitor(gym.make("Ant-v5", **custom_env_kwargs))
eval_env = Monitor(env)
print(eval_env.env.action_space)

mean_reward, std_reward = evaluate_policy(model, eval_env, n_eval_episodes=10)
print(f"{mean_reward = }, {std_reward = }")

# mean_reward, std_reward = evaluate_policy(model, vec_env, n_eval_episodes=10)
# print(f"{mean_reward = }, {std_reward = }")

env.close()
eval_env.close()
# vec_env.close()

Box(-1.0, 1.0, (8,), float32)
mean_reward = np.float64(974.5901590000001), std_reward = np.float64(14.484627731103082)
CPU times: user 13.6 s, sys: 35.9 ms, total: 13.6 s
Wall time: 13.8 s


In [ ]:
algo_name = type(model).__name__
env_name = env.spec.id
file_name = f"{algo_name}_{env_name}"

path_to_save_model = os.path.join(log_dir, file_name)

model.save(path_to_save_model)

# Подбор гиперпараметров

In [ ]:
# %whos

UsageError: Line magic function `%whos;` not found.


In [ ]:
env_id = "Ant-v5"
budget_to_learn = 30_000

new_budget = 10 * budget_to_learn

In [ ]:
%%time
ppo_model = PPO("MlpPolicy", env_id, seed=0, verbose=0)
ppo_model.learn(new_budget, progress_bar=True)

NameError: name 'PPO' is not defined

In [ ]:
%%time
eval_envs = make_vec_env(env_id, n_envs=10)
mean_reward, std_reward = evaluate_policy(ppo_model, eval_envs, n_eval_episodes=100, deterministic=True)

print(f"PPO Mean episode reward: {mean_reward:.2f} +/- {std_reward:.2f}")

NameError: name 'env_id' is not defined

In [ ]:
tuned_params = {
    "gamma": 0.9,
    "use_sde": True,
    "sde_sample_freq": 4,
    "learning_rate": 1e-3,
}

# budget = 10 * budget_pendulum
ppo_tuned_model = PPO("MlpPolicy", env_id, seed=1, verbose=1, **tuned_params).learn(50_000, log_interval=5)

Time to tune!

In [ ]:
import torch.nn as nn

In [ ]:
policy_kwargs = dict(
    net_arch=[
      dict(vf=[64, 64], pi=[64, 64]), # network architectures for actor/critic
    ],
    activation_fn=nn.Tanh,
)

hyperparams = dict(
    n_steps=5, # number of steps to collect data before updating policy
    learning_rate=7e-4,
    gamma=0.99, # discount factor
    max_grad_norm=0.5, # The maximum value for the gradient clipping
    ent_coef=0.0, # Entropy coefficient for the loss calculation
)

model = A2C("MlpPolicy", "CartPole-v1", seed=8, verbose=1, **hyperparams).learn(budget)

In [ ]:
mean_reward, std_reward = evaluate_policy(model, eval_envs_cartpole, n_eval_episodes=50, deterministic=True)

print(f"mean_reward:{mean_reward:.2f} +/- {std_reward:.2f}")

mean_reward:127.18 +/- 12.07


Hint - Recommended Hyperparameter Range

```python
gamma = trial.suggest_float("gamma", 0.9, 0.99999, log=True)
max_grad_norm = trial.suggest_float("max_grad_norm", 0.3, 5.0, log=True)
# from 2**3 = 8 to 2**10 = 1024
n_steps = 2 ** trial.suggest_int("exponent_n_steps", 3, 10)
learning_rate = trial.suggest_float("lr", 1e-5, 1, log=True)
ent_coef = trial.suggest_float("ent_coef", 0.00000001, 0.1, log=True)
# net_arch tiny: {"pi": [64], "vf": [64]}
# net_arch default: {"pi": [64, 64], "vf": [64, 64]}
# activation_fn = nn.Tanh / nn.ReLU
```

# Part III: Automatic Hyperparameter Tuning





In this part we will create a script that allows to search for the best hyperparameters automatically.

### Imports

In [ ]:
import optuna
from optuna.pruners import MedianPruner
from optuna.samplers import TPESampler
from optuna.visualization import plot_optimization_history, plot_param_importances

### Config

In [ ]:
N_TRIALS = 100  # Maximum number of trials
N_JOBS = 1 # Number of jobs to run in parallel
N_STARTUP_TRIALS = 5  # Stop random sampling after N_STARTUP_TRIALS
N_EVALUATIONS = 2  # Number of evaluations during the training
N_TIMESTEPS = int(2e4)  # Training budget
EVAL_FREQ = int(N_TIMESTEPS / N_EVALUATIONS)
N_EVAL_ENVS = 5
N_EVAL_EPISODES = 10
TIMEOUT = int(60 * 15)  # 15 minutes

ENV_ID = "CartPole-v1"

DEFAULT_HYPERPARAMS = {
    "policy": "MlpPolicy",
    "env": ENV_ID,
}

### Exercise (5 minutes): Define the search space

In [ ]:
from typing import Any, Dict
import torch
import torch.nn as nn

def sample_a2c_params(trial: optuna.Trial) -> Dict[str, Any]:
    """
    Sampler for A2C hyperparameters.

    :param trial: Optuna trial object
    :return: The sampled hyperparameters for the given trial.
    """
    # Discount factor between 0.9 and 0.9999
    gamma = 1.0 - trial.suggest_float("gamma", 0.0001, 0.1, log=True)
    max_grad_norm = trial.suggest_float("max_grad_norm", 0.3, 5.0, log=True)
    # 8, 16, 32, ... 1024
    n_steps = 2 ** trial.suggest_int("exponent_n_steps", 3, 10)

    ### YOUR CODE HERE
    # TODO:
    # - define the learning rate search space [1e-5, 1] (log) -> `suggest_float`
    # - define the network architecture search space ["tiny", "small"] -> `suggest_categorical`
    # - define the activation function search space ["tanh", "relu"]
    learning_rate = trial.suggest_float("lr", 1e-5, 1, log=True)
    net_arch = trial.suggest_categorical("net_arch", ["tiny", "small"])
    activation_fn = trial.suggest_categorical("activation_fn", ["tanh", "relu"])

    ### END OF YOUR CODE

    # Display true values
    trial.set_user_attr("gamma_", gamma)
    trial.set_user_attr("n_steps", n_steps)

    net_arch = [
        {"pi": [64], "vf": [64]}
        if net_arch == "tiny"
        else {"pi": [64, 64], "vf": [64, 64]}
    ]

    activation_fn = {"tanh": nn.Tanh, "relu": nn.ReLU}[activation_fn]

    return {
        "n_steps": n_steps,
        "gamma": gamma,
        "learning_rate": learning_rate,
        "max_grad_norm": max_grad_norm,
        "policy_kwargs": {
            "net_arch": net_arch,
            "activation_fn": activation_fn,
        },
    }

### Define the objective function

First we define a custom callback to report the results of periodic evaluations to Optuna:

In [ ]:
from stable_baselines3.common.callbacks import EvalCallback

class TrialEvalCallback(EvalCallback):
    """
    Callback used for evaluating and reporting a trial.

    :param eval_env: Evaluation environement
    :param trial: Optuna trial object
    :param n_eval_episodes: Number of evaluation episodes
    :param eval_freq:   Evaluate the agent every ``eval_freq`` call of the callback.
    :param deterministic: Whether the evaluation should
        use a stochastic or deterministic policy.
    :param verbose:
    """

    def __init__(
        self,
        eval_env: gym.Env,
        trial: optuna.Trial,
        n_eval_episodes: int = 5,
        eval_freq: int = 10000,
        deterministic: bool = True,
        verbose: int = 0,
    ):

        super().__init__(
            eval_env=eval_env,
            n_eval_episodes=n_eval_episodes,
            eval_freq=eval_freq,
            deterministic=deterministic,
            verbose=verbose,
        )
        self.trial = trial
        self.eval_idx = 0
        self.is_pruned = False

    def _on_step(self) -> bool:
        if self.eval_freq > 0 and self.n_calls % self.eval_freq == 0:
            # Evaluate policy (done in the parent class)
            super()._on_step()
            self.eval_idx += 1
            # Send report to Optuna
            self.trial.report(self.last_mean_reward, self.eval_idx)
            # Prune trial if need
            if self.trial.should_prune():
                self.is_pruned = True
                return False
        return True

### Exercise (10 minutes): Define the objective function

Then we define the objective function that is in charge of sampling hyperparameters, creating the model and then returning the result to Optuna

In [ ]:
def objective(trial: optuna.Trial) -> float:
    """
    Objective function using by Optuna to evaluate
    one configuration (i.e., one set of hyperparameters).

    Given a trial object, it will sample hyperparameters,
    evaluate it and report the result (mean episodic reward after training)

    :param trial: Optuna trial object
    :return: Mean episodic reward after training
    """

    kwargs = DEFAULT_HYPERPARAMS.copy()
    ### YOUR CODE HERE
    # TODO:
    # 1. Sample hyperparameters and update the default keyword arguments: `kwargs.update(other_params)`
    # 2. Create the evaluation envs
    # 3. Create the `TrialEvalCallback`

    # 1. Sample hyperparameters and update the keyword arguments
    kwargs.update(sample_a2c_params(trial))
    # Create the RL model
    model = A2C(**kwargs)

    # 2. Create envs used for evaluation using `make_vec_env`, `ENV_ID` and `N_EVAL_ENVS`
    eval_env = make_vec_env(ENV_ID, N_EVAL_ENVS)

    # 3. Create the `TrialEvalCallback` callback defined above that will periodically evaluate
    # and report the performance using `N_EVAL_EPISODES` every `EVAL_FREQ`
    # TrialEvalCallback signature:
    # TrialEvalCallback(eval_env, trial, n_eval_episodes, eval_freq, deterministic, verbose)
    eval_callback = TrialEvalCallback(eval_env, trial, N_EVAL_EPISODES, EVAL_FREQ)

    ### END OF YOUR CODE

    nan_encountered = False
    try:
        # Train the model
        model.learn(N_TIMESTEPS, callback=eval_callback)
    except AssertionError as e:
        # Sometimes, random hyperparams can generate NaN
        print(e)
        nan_encountered = True
    finally:
        # Free memory
        model.env.close()
        eval_envs.close()

    # Tell the optimizer that the trial failed
    if nan_encountered:
        return float("nan")

    if eval_callback.is_pruned:
        raise optuna.exceptions.TrialPruned()

    return eval_callback.last_mean_reward

### The optimization loop

In [ ]:
import torch as th

# Set pytorch num threads to 1 for faster training
th.set_num_threads(1)
# Select the sampler, can be random, TPESampler, CMAES, ...
sampler = TPESampler(n_startup_trials=N_STARTUP_TRIALS)
# Do not prune before 1/3 of the max budget is used
pruner = MedianPruner(
    n_startup_trials=N_STARTUP_TRIALS, n_warmup_steps=N_EVALUATIONS // 3
)
# Create the study and start the hyperparameter optimization
study = optuna.create_study(sampler=sampler, pruner=pruner, direction="maximize")

try:
    study.optimize(objective, n_trials=N_TRIALS, n_jobs=N_JOBS, timeout=TIMEOUT)
except KeyboardInterrupt:
    pass

print("Number of finished trials: ", len(study.trials))

print("Best trial:")
trial = study.best_trial

print(f"  Value: {trial.value}")

print("  Params: ")
for key, value in trial.params.items():
    print(f"    {key}: {value}")

print("  User attrs:")
for key, value in trial.user_attrs.items():
    print(f"    {key}: {value}")

# Write report
study.trials_dataframe().to_csv("study_results_a2c_cartpole.csv")

fig1 = plot_optimization_history(study)
fig2 = plot_param_importances(study)

fig1.show()
fig2.show()

[I 2025-05-07 10:53:09,427] A new study created in memory with name: no-name-2390910c-65d0-43ce-a89e-bbb9fac5cf1e
/usr/local/lib/python3.11/dist-packages/stable_baselines3/common/policies.py:486: UserWarning: As shared layers in the mlp_extractor are removed since SB3 v1.8.0, you should now pass directly a dictionary and not a list (net_arch=dict(pi=..., vf=...) instead of net_arch=[dict(pi=..., vf=...)])
  warnings.warn(
[I 2025-05-07 10:53:33,361] Trial 0 finished with value: 9.5 and parameters: {'gamma': 0.0003099438349093253, 'max_grad_norm': 0.349286144389617, 'exponent_n_steps': 7, 'lr': 0.03629519260852455, 'net_arch': 'small', 'activation_fn': 'relu'}. Best is trial 0 with value: 9.5.
[I 2025-05-07 10:53:51,088] Trial 1 finished with value: 9.2 and parameters: {'gamma': 0.00017180160666983472, 'max_grad_norm': 4.787011145782151, 'exponent_n_steps': 9, 'lr': 0.24675940543343836, 'net_arch': 'tiny', 'activation_fn': 'relu'}. Best is trial 0 with value: 9.5.
[I 2025-05-07 10:54:18

Number of finished trials:  52
Best trial:
  Value: 500.0
  Params: 
    gamma: 0.043022953996323075
    max_grad_norm: 2.127581402889809
    exponent_n_steps: 4
    lr: 0.005040804466756703
    net_arch: tiny
    activation_fn: relu
  User attrs:
    gamma_: 0.956977046003677
    n_steps: 16


Complete example: https://github.com/DLR-RM/rl-baselines3-zoo

# Conclusion

What we have seen in this notebook:
- the importance of good hyperparameters
- how to do automatic hyperparameter search with optuna




---



# Optuna use example from Arrafin [post](https://araffin.github.io/post/optuna/)

In [ ]:
"""Optuna example that optimizes the hyperparameters of
a reinforcement learning agent using PPO implementation from Stable-Baselines3
on a Gymnasium environment.

This is a simplified version of what can be found in https://github.com/DLR-RM/rl-baselines3-zoo.

You can run this example as follows:
    $ python optimize_ppo.py

"""

from typing import Any

import gymnasium
import optuna
from optuna.pruners import MedianPruner
from optuna.samplers import TPESampler
from stable_baselines3 import PPO
from stable_baselines3.common.callbacks import EvalCallback
from stable_baselines3.common.env_util import make_vec_env
import torch
import torch.nn as nn


N_TRIALS = 500
N_STARTUP_TRIALS = 10
N_EVALUATIONS = 2
N_TIMESTEPS = 40_000
EVAL_FREQ = int(N_TIMESTEPS / N_EVALUATIONS)
N_EVAL_EPISODES = 10

ENV_ID = "Pendulum-v1"
N_ENVS = 5

DEFAULT_HYPERPARAMS = {
    "policy": "MlpPolicy",
}


def sample_ppo_params(trial: optuna.Trial) -> dict[str, Any]:
    """Sampler for PPO hyperparameters."""
    # From 2**5=32 to 2**12=4096
    n_steps_pow = trial.suggest_int("n_steps_pow", 5, 12)
    gamma = trial.suggest_float("gamma", 0.97, 0.9999)
    learning_rate = trial.suggest_float("learning_rate", 3e-5, 3e-3, log=True)
    activation_fn = trial.suggest_categorical("activation_fn", ["tanh", "relu"])

    n_steps = 2**n_steps_pow
    # Display true values
    trial.set_user_attr("n_steps", n_steps)
    # Convert to PyTorch objects
    activation_fn = {"tanh": nn.Tanh, "relu": nn.ReLU}[activation_fn]

    return {
        "n_steps": n_steps,
        "gamma": gamma,
        "learning_rate": learning_rate,
        "policy_kwargs": {
            "activation_fn": activation_fn,
        },
    }


class TrialEvalCallback(EvalCallback):
    """Callback used for evaluating and reporting a trial."""

    def __init__(
        self,
        eval_env: gymnasium.Env,
        trial: optuna.Trial,
        n_eval_episodes: int = 5,
        eval_freq: int = 10000,
        deterministic: bool = True,
        verbose: int = 0,
    ):
        super().__init__(
            eval_env=eval_env,
            n_eval_episodes=n_eval_episodes,
            eval_freq=eval_freq,
            deterministic=deterministic,
            verbose=verbose,
        )
        self.trial = trial
        self.eval_idx = 0
        self.is_pruned = False

    def _on_step(self) -> bool:
        if self.eval_freq > 0 and self.n_calls % self.eval_freq == 0:
            super()._on_step()
            self.eval_idx += 1
            self.trial.report(self.last_mean_reward, self.eval_idx)
            # Prune trial if need.
            if self.trial.should_prune():
                self.is_pruned = True
                return False
        return True


def objective(trial: optuna.Trial) -> float:
    vec_env = make_vec_env(ENV_ID, n_envs=N_ENVS)
    kwargs = DEFAULT_HYPERPARAMS.copy()
    # Sample hyperparameters.
    kwargs.update(sample_ppo_params(trial))
    # Create the RL model.
    model = PPO(env=vec_env, **kwargs)
    # Create env used for evaluation.
    eval_env = make_vec_env(ENV_ID, n_envs=N_ENVS)
    # Create the callback that will periodically evaluate and report the performance.
    eval_callback = TrialEvalCallback(
        eval_env,
        trial,
        n_eval_episodes=N_EVAL_EPISODES,
        eval_freq=max(EVAL_FREQ // N_ENVS, 1),
        deterministic=True,
    )

    nan_encountered = False
    try:
        model.learn(N_TIMESTEPS, callback=eval_callback)
    except AssertionError as e:
        # Sometimes, random hyperparams can generate NaN.
        print(e)
        nan_encountered = True
    finally:
        # Free memory.
        model.env.close()
        eval_env.close()

    # Tell the optimizer that the trial failed.
    if nan_encountered:
        return float("nan")

    if eval_callback.is_pruned:
        raise optuna.exceptions.TrialPruned()

    return eval_callback.last_mean_reward


if __name__ == "__main__":
    # Set pytorch num threads to 1 for faster training.
    torch.set_num_threads(1)

    sampler = TPESampler(n_startup_trials=N_STARTUP_TRIALS, multivariate=True)
    # Do not prune before 1/3 of the max budget is used.
    pruner = MedianPruner(
        n_startup_trials=N_STARTUP_TRIALS, n_warmup_steps=N_EVALUATIONS // 3
    )

    study = optuna.create_study(sampler=sampler, pruner=pruner, direction="maximize")
    try:
        study.optimize(objective, n_trials=N_TRIALS, timeout=600)
    except KeyboardInterrupt:
        pass

    print(f"Number of finished trials: {len(study.trials)}")

    print("Best trial:")
    trial = study.best_trial

    print("  Value: ", trial.value)

    print("  Params: ")
    for key, value in trial.params.items():
        print(f"    {key}: {value}")

    print("  User attrs:")
    for key, value in trial.user_attrs.items():
        print(f"    {key}: {value}")

/usr/local/lib/python3.11/dist-packages/optuna/_experimental.py:31: ExperimentalWarning: Argument ``multivariate`` is an experimental feature. The interface can change in the future.
  warnings.warn(
[I 2025-05-07 06:23:50,486] A new study created in memory with name: no-name-ec51315d-b57f-4e1d-8172-06178f875f08
[I 2025-05-07 06:24:22,000] Trial 0 finished with value: -1104.8031417 and parameters: {'n_steps_pow': 11, 'gamma': 0.9717752594505243, 'learning_rate': 0.0009183829962213949, 'activation_fn': 'tanh'}. Best is trial 0 with value: -1104.8031417.
[I 2025-05-07 06:24:52,831] Trial 1 finished with value: -1403.2242927 and parameters: {'n_steps_pow': 8, 'gamma': 0.9956854702881278, 'learning_rate': 0.00017373306505887276, 'activation_fn': 'relu'}. Best is trial 0 with value: -1104.8031417.
[I 2025-05-07 06:25:24,747] Trial 2 finished with value: -1461.2066082000003 and parameters: {'n_steps_pow': 6, 'gamma': 0.9735116678394656, 'learning_rate': 3.3852430611972214e-05, 'activation_fn

Number of finished trials: 19
Best trial:
  Value:  -163.77188689999997
  Params: 
    n_steps_pow: 8
    gamma: 0.9749712609115107
    learning_rate: 0.0018765871621028618
    activation_fn: relu
  User attrs:
    n_steps: 256
